In [62]:
import bokeh
from bokeh.plotting import figure, show, output_notebook
from bokeh.charts import Scatter, Line, color
from bokeh import palettes
from bokeh.layouts import row
output_notebook()

import numpy as np
import pandas as pd
import os
import math
import time
from IPython.display import clear_output

colors = palettes.Paired12
basedirs = ['/Volumes/dev/code/structure-experiments/results',
            '/Volumes/speedy/code/structure-experiments/results',
            '/Volumes/wwhitney/structure-experiments/results']

tooltips = [
    ('Experiment', '@experiment'),
    ('Step', '@step'),
    ('Loss', '@loss'),
    ('Prior divergence', '@priordivergence'),
    ('Transition divergence', '@transdivergence'),
]

Loading BokehJS ...

In [63]:
def movingaverage(steps, values, window_size):
    window = np.ones(int(window_size))/float(window_size)

    smooth_values = np.convolve(values, window, 'valid')
    padding = int((len(steps) - len(smooth_values)) / 2)
    aligned_steps = steps[padding : len(steps) - padding]
    return aligned_steps, smooth_values

def sparsify(steps, values, amount):
    if amount < 2: return steps, values
    sparse_steps = []
    sparse_values = []

    for i in range(min(len(steps), len(values))):
        if i % amount == 0:
            sparse_values.append(values[i])
            sparse_steps.append(steps[i])
    return np.array(sparse_steps), np.array(sparse_values)

In [64]:
def load_result_df(experiment):
    for basedir in basedirs:
        df = pd.DataFrame()
        try:
            path = os.path.join(basedir, experiment, 'results.csv')
            df = pd.read_csv(path, error_bad_lines=False)
            if len(df) > 0:
                break
        except Exception as e:
            print("Error in parsing experiment {} from basedir {}:".format(experiment, basedir), e)
            continue

    numeric_columns = list(df.columns)
#     numeric_columns.remove('experiment')
    df[numeric_columns] = df[numeric_columns].apply(pd.to_numeric, errors="coerce")
    
    for col in df:
        df["".join(col.split()).lower()] = df[col]
#         df[col.strip().lower()] = df[col]
    df['experiment'] = pd.Series([experiment] * len(df), index=df.index)
    return df

def make_dataframe(results):
    data = pd.DataFrame()
    for experiment in results:
        single_df = load_result_df(experiment)
#         print(single_df)
        data = data.append(single_df, ignore_index=True)
#         print(data)
    return data

In [ ]:
networks = [
    "breakout_skip5_z4_3e4_2",
    "breakout_skip5_z4_3e4_4",
    "breakout_skip5_z4_3e4_3",
    "breakout_skip5_z4_3e4_1",
]

data = make_dataframe(networks)
for facet in ['loss', 'trans divergence']:
    plot = Line(data, x='step', y=facet, 
                color=color(columns='experiment', palette=palettes.Spectral11),
                tools='pan,wheel_zoom,box_zoom,save,reset', 
                active_scroll="wheel_zoom",
                tooltips=tooltips,
                plot_width=900,
                plot_height=600)
    show(plot)

In [ ]:
networks = [
    "urban_z4_3e5_1",
    "urban_z4_1e4_1",
    "urban_z4_3e4_1",
    "urban_z4_1e3_1",
]

data = make_dataframe(networks)
spaced_palette = palettes.linear_palette(palettes.Spectral11, len(networks))
for facet in ['loss', 'trans divergence']:
    plot = Line(data, x='step', y=facet, title="urban",
                color=color(columns='experiment', palette=spaced_palette),
                tools='pan,wheel_zoom,box_zoom,save,reset', 
                active_scroll="wheel_zoom",
                tooltips=tooltips,
                plot_width=900,
                plot_height=600)
    show(plot)

In [ ]:
networks = [
#     "urban_128_z8_3e5_1",
#     "urban_128_z8_1e4_1",
#     "urban_128_z8_3e4_1",
#     "urban_128_z8_1e3_1",
#     "urban_128_dcgan_z8_3e5_1",
#     "urban_128_dcgan_z8_1e4_1",
#     "urban_128_dcgan_z8_3e5_1_restart",
#     "urban_128_dcgan_z8_1e4_1_restart",
#     "urban_128_dcgan_z8_3e4_1_restart",
#     "urban_128_dcgan_z8_1e3_1",
    
#     "urban_128_dcgan_z8_3e4_1",
#     "urban_128_dcgan_z8_1e4_2",
#     "urban_128_dcgan_z8_3e4_2",
#     "urban_128_dcgan_z4_3e4_1",
#     "urban_128_dcgan_z8_shallowtrans_3e4",

#     "urban_2fps_128_dcgan_z8_var0.02_3e4_1",
#     "urban_2fps_128_dcgan_z8_3e4_1",
    
    "urban_2fps_128_dcgan_z8_3e4_2",
    "urban_2fps_128_dcgan_z8_var0.05_3e4_1",
    "urban_2fps_128_dcgan_z8_var0.1_3e4_1",
#     "urban_2fps_128_dcgan_z8_var0.05_gradscale_3e4_1",
    
    "urban_2fps_128_dcgan_z8_var0.05_3e4_2",
    "urban_2fps_128_dcgan_z8_var0.1_3e4_2",
    "urban_2fps_128_dcgan_z1_var0.05_3e4_1",
    "urban_2fps_128_dcgan_z20_h10_var0.05_3e4_1",
]

palette = palettes.Spectral11[:5] + palettes.Spectral11[6:]
data = make_dataframe(networks)
spaced_palette = palettes.linear_palette(palette, len(networks))
for facet in ['loss', 'trans divergence']:
    plot = Line(data, x='step', y=facet, title="urban",
                color=color(columns='experiment', palette=spaced_palette),
                tools='pan,wheel_zoom,box_zoom,save,reset', 
                active_scroll="wheel_zoom",
                tooltips=tooltips,
                plot_width=900,
                plot_height=600,
                legend='top_right')
#     if facet == 'loss':
#         plot.y_range = bokeh.models.Range1d(-70000, -60000)
    if facet == 'trans divergence':
        plot.y_range = bokeh.models.Range1d(0, 80)
    show(plot)

In [98]:
networks = [    
    "urban_2fps_128_dcgan_z20_h10_var0.05_3e4_2_",
    "urban_2fps_128_dcgan_z8_var0.05_3e4_3_",
    "urban_2fps_128_dcgan_z1_var0.05_3e4_2_",
    "urban_2fps_128_dcgan_z8_var0.1_3e4_3_",
]

palette = palettes.Spectral11[:5] + palettes.Spectral11[6:]
data = make_dataframe(networks)
spaced_palette = palettes.linear_palette(palette, len(networks))
for facet in ['loss', 'trans divergence']:
    plot = Line(data, x='step', y=facet, title="urban",
                color=color(columns='experiment', palette=spaced_palette),
                tools='pan,wheel_zoom,box_zoom,save,reset', 
                active_scroll="wheel_zoom",
                tooltips=tooltips,
                plot_width=900,
                plot_height=600,
                legend='top_right')
#     if facet == 'loss':
#         plot.y_range = bokeh.models.Range1d(-70000, -60000)
    if facet == 'trans divergence':
        plot.y_range = bokeh.models.Range1d(0, 80)
    show(plot)

In [99]:
networks = [    
#     "freeway_128_dcgan_z8_var0.1_3e4_1_",
#     "freeway_128_dcgan_z1_var0.05_3e4_1_",
#     "freeway_128_dcgan_z8_var0.05_3e4_1_",
#     "freeway_128_dcgan_z20_h10_var0.05_3e4_1_",
    "breakout_128_dcgan_z8_var0.1_3e4_1",
    "breakout_128_dcgan_z8_var0.05_3e4_1",
    "breakout_128_dcgan_z1_var0.05_3e4_1",
    "breakout_128_dcgan_z20_h10_var0.05_3e4_1",

]

palette = palettes.Spectral11[:5] + palettes.Spectral11[6:]
data = make_dataframe(networks)
spaced_palette = palettes.linear_palette(palette, len(networks))
for facet in ['loss', 'trans divergence']:
    plot = Line(data, x='step', y=facet, title="atari",
                color=color(columns='experiment', palette=spaced_palette),
                tools='pan,wheel_zoom,box_zoom,save,reset', 
                active_scroll="wheel_zoom",
                tooltips=tooltips,
                plot_width=900,
                plot_height=600,
                legend='top_right')
#     if facet == 'loss':
#         plot.y_range = bokeh.models.Range1d(-70000, -60000)
    if facet == 'trans divergence':
        plot.y_range = bokeh.models.Range1d(0, 80)
    show(plot)

Error in parsing result: File b'/Volumes/speedy/code/structure-experiments/results/breakout_128_dcgan_z8_var0.1_3e4_1/results.csv' does not exist
Error in parsing result: File b'/Volumes/speedy/code/structure-experiments/results/breakout_128_dcgan_z8_var0.05_3e4_1/results.csv' does not exist
Error in parsing result: File b'/Volumes/speedy/code/structure-experiments/results/breakout_128_dcgan_z1_var0.05_3e4_1/results.csv' does not exist
Error in parsing result: File b'/Volumes/speedy/code/structure-experiments/results/breakout_128_dcgan_z20_h10_var0.05_3e4_1/results.csv' does not exist


In [18]:

networks = [    
    "urban_bvae5_klend6e6_hvar0.05_3e4_1_",
    "urban_bvae2_klend6e6_hvar0.05_3e4_1_",
    "urban_bvae5_klend3e6_hvar0.05_3e4_1",
    "urban_bvae2_klend3e6_hvar0.05_3e4_1_",
]

palette = palettes.Spectral11[:5] + palettes.Spectral11[6:]
data = make_dataframe(networks)
spaced_palette = palettes.linear_palette(palette, len(networks))
for facet in ['loss', 'trans divergence']:
    plot = Line(data, x='step', y=facet, title="recurrent B-VAE",
                color=color(columns='experiment', palette=spaced_palette),
                tools='pan,wheel_zoom,box_zoom,save,reset', 
                active_scroll="wheel_zoom",
                tooltips=tooltips,
                plot_width=900,
                plot_height=600,
                legend='top_right')
#     if facet == 'loss':
#         plot.y_range = bokeh.models.Range1d(-70000, -60000)
    if facet == 'trans divergence':
        plot.y_range = bokeh.models.Range1d(0, 80)
    show(plot)

Error in parsing result: File b'/Volumes/dev/code/structure-experiments/results/urban_bvae5_klend6e6_hvar0.05_3e4_1_/results.csv' does not exist
Error in parsing result: File b'/Volumes/speedy/code/structure-experiments/results/urban_bvae5_klend6e6_hvar0.05_3e4_1_/results.csv' does not exist
Error in parsing result: File b'/Volumes/dev/code/structure-experiments/results/urban_bvae2_klend6e6_hvar0.05_3e4_1_/results.csv' does not exist
Error in parsing result: File b'/Volumes/speedy/code/structure-experiments/results/urban_bvae2_klend6e6_hvar0.05_3e4_1_/results.csv' does not exist
Error in parsing result: File b'/Volumes/dev/code/structure-experiments/results/urban_bvae5_klend3e6_hvar0.05_3e4_1/results.csv' does not exist
Error in parsing result: File b'/Volumes/speedy/code/structure-experiments/results/urban_bvae5_klend3e6_hvar0.05_3e4_1/results.csv' does not exist
Error in parsing result: File b'/Volumes/dev/code/structure-experiments/results/urban_bvae2_klend3e6_hvar0.05_3e4_1_/result

In [159]:
networks = [    
#     "balls6_width16_var0.05_3e4_1",
#     "balls6_width16_var0.1_klend_1e6_3e4_1",
#     "balls6_width16_var0.1_3e4_1",
#     "balls6_width16_var0.01_3e4_1",
#     "balls6_width16_z6_h10_var0.1_3e4_1",
#     "balls6_width16_z6_h10_var0.01_3e4_1",
#     "balls6_width16_z12_h5_var0.1_3e4_1",
#     "balls6_width16_z12_h5_var0.01_3e4_1",
    
#     "balls6_width16_nokl_var0.01_1e4_1",
#     "balls6_width16_nokl_var0.1_1e4_1",
#     "balls6_width16_shallowtrans_var0.01_3e4_1",
#     "balls6_width16_shallowtrans_z12_h5_var0.01_1e4_1",
#     "balls6_width16_shallowtrans_var0.01_1e4_1",
#     "balls6_width16_nokl_var0.1_3e4_1",
#     "balls6_width16_nokl_var0.01_3e4_1",
#     "balls6_width16_shallowtrans_var0.1_3e4_1",
    
#     "balls6_width16_z12_h5_var0.01_3e4_1",
#     "balls6_width16_var0.1_3e4_1",
#     "balls6_width16_z12_h5_var0.01_1e4_1",
#     "balls6_width16_var0.01_1e4_1",
#     "balls6_width16_var0.01_3e4_1",
#     "balls6_width16_nokl_var0.1_3e4_1",
#     "balls6_width16_nokl_var0.01_3e4_1",
    
#     "6balls_width8_var0.1_3e4_1",
#     "4balls_width8_var0.1_3e4_1",
#     "2balls_width8_var0.1_3e4_1",
#     "6balls_width8_var0.05_1e4_1",
#     "4balls_width8_var0.05_1e4_1",
#     "2balls_width8_var0.05_1e4_1",
#     "6balls_width8_var0.05_3e4_1",
#     "6balls_width8_var0.01_3e4_1",
#     "4balls_width8_var0.05_3e4_1",
#     "4balls_width8_var0.01_3e4_1",
#     "2balls_width8_var0.01_3e4_1",
    "2balls_width8_var0.05_3e4_1",
    
    "2balls_bigmodel_z6_h50_var0.01_3e4_1",
    "2balls_bigmodel_z4_h50_var0.01_3e4_1",
    "2balls_bigmodel_z2_h50_var0.01_3e4_1",
    "2balls_bigmodel_z6_var0.01_3e4_1",
    "2balls_bigmodel_z6_h10_var0.01_3e4_1",
    "2balls_bigmodel_z4_h10_var0.01_3e4_1",
    "2balls_bigmodel_z2_h10_var0.01_3e4_1",
    "2balls_bigmodel_z2_var0.01_3e4_1",
    "2balls_bigmodel_var0.01_3e4_1",
    "color_2ball_3e4_2"
]

# palette = palettes.Spectral11[:5] + palettes.Spectral11[6:]
data = make_dataframe(networks)
data.ix[data.experiment=="color_2ball_3e4_2", 'step'] = data.ix[data.experiment=="color_2ball_3e4_2", 'step'] * 32
# spaced_palette = palettes.linear_palette(palette, len(networks))
for facet in ['loss', 'trans divergence']:
# for facet in ['trans divergence']:
    plot = Line(data, x='step', y=facet, title="balls",
                color=color(columns='experiment'),
                tools='pan,wheel_zoom,box_zoom,save,reset', 
                active_scroll="wheel_zoom",
                tooltips=tooltips,
                plot_width=900,
                plot_height=600,
                legend='top_right')
#     if facet == 'loss':
#         plot.y_range = bokeh.models.Range1d(-70000, -60000)
    if facet == 'trans divergence':
        plot.y_range = bokeh.models.Range1d(-5, 40)
    show(plot)

In [16]:
networks = [    
#     "5thave_128_dcgan_z1_var0.05_3e4_1",
#     "5thave_128_dcgan_z8_var0.1_3e4_1",
#     "5thave_128_dcgan_z8_var0.05_3e4_1",
#     "5thave_128_dcgan_z20_h10_var0.05_3e4_1",


#     "5thave_128_dcgan_z8_var0.2_1e3_1",
#     "5thave_128_dcgan_nodecay_z8_var0.2_3e3_1",
#     "5thave_128_dcgan_z8_var0.2_3e3_1",
#     "5thave_128_dcgan_nodecay_z8_var0.2_1e3_1",
#     "5thave_128_dcgan_z8_var0.3_1e3_1",
    
    "5thave_128_dcgan_nodecay_z8_var0.2_3e4_1",
    "5thave_128_dcgan_z8_var0.2_6e4_1",
    "5thave_128_dcgan_nodecay_z8_var0.2_6e4_1",
    "5thave_128_dcgan_z8_var0.2_3e4_2",
]

palette = palettes.Spectral11[:5] + palettes.Spectral11[6:]
data = make_dataframe(networks)
spaced_palette = palettes.linear_palette(palette, len(networks))
for facet in ['loss', 'trans divergence']:
    plot = Line(data, x='step', y=facet, title="5th ave optimization search",
                color=color(columns='experiment', palette=spaced_palette),
                tools='pan,wheel_zoom,box_zoom,save,reset', 
                active_scroll="wheel_zoom",
                tooltips=tooltips,
                plot_width=900,
                plot_height=600,
                legend='top_right')
#     if facet == 'loss':
#         plot.y_range = bokeh.models.Range1d(-70000, -60000)
    if facet == 'trans divergence':
        plot.y_range = bokeh.models.Range1d(0, 80)
    show(plot)

Error in parsing result: File b'/Volumes/dev/code/structure-experiments/results/5thave_128_dcgan_nodecay_z8_var0.2_3e4_1/results.csv' does not exist
Error in parsing result: File b'/Volumes/dev/code/structure-experiments/results/5thave_128_dcgan_z8_var0.2_6e4_1/results.csv' does not exist
Error in parsing result: File b'/Volumes/dev/code/structure-experiments/results/5thave_128_dcgan_nodecay_z8_var0.2_6e4_1/results.csv' does not exist
Error in parsing result: File b'/Volumes/dev/code/structure-experiments/results/5thave_128_dcgan_z8_var0.2_3e4_2/results.csv' does not exist


In [5]:
networks = [    
#     "5thave_128_dcgan_z1_var0.05_3e4_1",
#     "5thave_128_dcgan_z8_var0.1_3e4_1",
#     "5thave_128_dcgan_z8_var0.05_3e4_1",
#     "5thave_128_dcgan_z20_h10_var0.05_3e4_1",

    "5thave_128_dcgan_z8_var0.2_3e4_1",
    "5thave_128_dcgan_z20_h10_var0.2_3e4_1",
    "5thave_128_dcgan_z8_var0.2_1e3_1",
    "5thave_128_dcgan_z8_var0.2_1e4_1",
]

palette = palettes.Spectral11[:5] + palettes.Spectral11[6:]
data = make_dataframe(networks)
spaced_palette = palettes.linear_palette(palette, len(networks))
for facet in ['loss', 'trans divergence']:
    plot = Line(data, x='step', y=facet, title="5th ave",
                color=color(columns='experiment', palette=spaced_palette),
                tools='pan,wheel_zoom,box_zoom,save,reset', 
                active_scroll="wheel_zoom",
                tooltips=tooltips,
                plot_width=900,
                plot_height=600,
                legend='top_right')
#     if facet == 'loss':
#         plot.y_range = bokeh.models.Range1d(-70000, -60000)
    if facet == 'trans divergence':
        plot.y_range = bokeh.models.Range1d(0, 80)
    show(plot)

Error in parsing result: File b'/Volumes/dev/code/structure-experiments/results/5thave_128_dcgan_z8_var0.2_3e4_1/results.csv' does not exist
Error in parsing result: File b'/Volumes/speedy/code/structure-experiments/results/5thave_128_dcgan_z8_var0.2_3e4_1/results.csv' does not exist
Error in parsing result: File b'/Volumes/dev/code/structure-experiments/results/5thave_128_dcgan_z20_h10_var0.2_3e4_1/results.csv' does not exist
Error in parsing result: File b'/Volumes/speedy/code/structure-experiments/results/5thave_128_dcgan_z20_h10_var0.2_3e4_1/results.csv' does not exist
Error in parsing result: File b'/Volumes/dev/code/structure-experiments/results/5thave_128_dcgan_z8_var0.2_1e3_1/results.csv' does not exist
Error in parsing result: File b'/Volumes/speedy/code/structure-experiments/results/5thave_128_dcgan_z8_var0.2_1e3_1/results.csv' does not exist
Error in parsing result: File b'/Volumes/dev/code/structure-experiments/results/5thave_128_dcgan_z8_var0.2_1e4_1/results.csv' does not 

In [17]:
networks = [    
#     "urban_z20_h25",
#     "urban_z2_h25",
#     "urban_z8_h50",
#     "urban_z8_h10",

#     "urban_z2_h25_var0.1",
#     "urban_z8_h50_var0.1",
#     "urban_z8_h10_var0.1",
#     "urban_z20_h25_var0.1",
    
#     "5thave_deeptrans_z8_h50_var0.2",
#     "5thave_z20_h25_var0.2_1e3",
#     "5thave_z4_h200_var0.2_1e3",
#     "5thave_z8_h50_var0.2_1e3",
    "5thave_z8_h50_var0.2_6e4",
    "5thave_z4_h200_var0.2_6e4",
    "5thave_z20_h25_var0.2_6e4",
    "5thave_deeptrans_z8_h50_var0.2_6e4",
]

palette = palettes.Spectral11[:5] + palettes.Spectral11[6:]
data = make_dataframe(networks)
spaced_palette = palettes.linear_palette(palette, len(networks))
for facet in ['loss', 'trans divergence']:
    plot = Line(data, x='step', y=facet, title="5th ave weird sizes",
                color=color(columns='experiment', palette=spaced_palette),
                tools='pan,wheel_zoom,box_zoom,save,reset', 
                active_scroll="wheel_zoom",
                tooltips=tooltips,
                plot_width=900,
                plot_height=600,
                legend='top_right')
    if facet == 'loss':
        plot.y_range = bokeh.models.Range1d(5000, 7000)
    if facet == 'trans divergence':
        plot.y_range = bokeh.models.Range1d(0, 80)
    show(plot)

Error in parsing result: File b'/Volumes/dev/code/structure-experiments/results/5thave_z8_h50_var0.2_6e4/results.csv' does not exist
Error in parsing result: File b'/Volumes/dev/code/structure-experiments/results/5thave_z4_h200_var0.2_6e4/results.csv' does not exist
Error in parsing result: File b'/Volumes/dev/code/structure-experiments/results/5thave_z20_h25_var0.2_6e4/results.csv' does not exist
Error in parsing result: File b'/Volumes/dev/code/structure-experiments/results/5thave_deeptrans_z8_h50_var0.2_6e4/results.csv' does not exist


In [12]:
networks = [    
    "5thave_128_dcgan_deeptrans_z4_var0.1_3e4_1_",
    "5thave_128_dcgan_deeptrans_z4_var0.2_3e4_1_",
    "5thave_128_dcgan_deeptrans_z8_var0.1_3e4_1_",
    "5thave_128_dcgan_deeptrans_z8_var0.2_3e4_1_",

]

palette = palettes.Spectral11[:5] + palettes.Spectral11[6:]
data = make_dataframe(networks)
spaced_palette = palettes.linear_palette(palette, len(networks))
for facet in ['loss', 'trans divergence']:
    plot = Line(data, x='step', y=facet, title="5th ave deep transitions",
                color=color(columns='experiment', palette=spaced_palette),
                tools='pan,wheel_zoom,box_zoom,save,reset', 
                active_scroll="wheel_zoom",
                tooltips=tooltips,
                plot_width=900,
                plot_height=600,
                legend='top_right')
#     if facet == 'loss':
#         plot.y_range = bokeh.models.Range1d(-70000, -60000)
    if facet == 'trans divergence':
        plot.y_range = bokeh.models.Range1d(0, 80)
    show(plot)

Error in parsing result: File b'/Volumes/dev/code/structure-experiments/results/5thave_128_dcgan_deeptrans_z4_var0.1_3e4_1_/results.csv' does not exist
Error in parsing result: File b'/Volumes/dev/code/structure-experiments/results/5thave_128_dcgan_deeptrans_z4_var0.2_3e4_1_/results.csv' does not exist
Error in parsing result: File b'/Volumes/dev/code/structure-experiments/results/5thave_128_dcgan_deeptrans_z8_var0.1_3e4_1_/results.csv' does not exist
Error in parsing result: File b'/Volumes/dev/code/structure-experiments/results/5thave_128_dcgan_deeptrans_z8_var0.2_3e4_1_/results.csv' does not exist


In [57]:
networks = [       
    "5thave_bvae5_var0.05_6e4_1",
    "5thave_bvae2_var0.05_6e4_1",
    "5thave_bvae5_var0.2_6e4_1",
    "5thave_bvae2_var0.2_6e4_1",
]

palette = palettes.Spectral11[:5] + palettes.Spectral11[6:]
data = make_dataframe(networks)
spaced_palette = palettes.linear_palette(palette, len(networks))
plots = []
for facet in ['loss', 'prior divergence']:
    plot = Line(data, x='step', y=facet, title="5th ave BVAE" + ", " + facet,
                color=color(columns='experiment', palette=spaced_palette),
                tools='pan,wheel_zoom,box_zoom,save,reset', 
                active_scroll="wheel_zoom",
                tooltips=tooltips,
#                 plot_width=600,
#                 plot_height=600,
                legend='top_right')
#     if facet == 'loss':
#         plot.y_range = bokeh.models.Range1d(-70000, -60000)
    if facet == 'trans divergence':
        plot.y_range = bokeh.models.Range1d(0, 80)
#     show(plot)
    plots.append(plot)
show(row(children=plots, responsive=True)) #, sizing_mode="stretch_both"))

Error in parsing experiment 5thave_bvae5_var0.05_6e4_1 from basedir /Volumes/dev/code/structure-experiments/results: File b'/Volumes/dev/code/structure-experiments/results/5thave_bvae5_var0.05_6e4_1/results.csv' does not exist
Error in parsing experiment 5thave_bvae2_var0.05_6e4_1 from basedir /Volumes/dev/code/structure-experiments/results: File b'/Volumes/dev/code/structure-experiments/results/5thave_bvae2_var0.05_6e4_1/results.csv' does not exist
Error in parsing experiment 5thave_bvae5_var0.2_6e4_1 from basedir /Volumes/dev/code/structure-experiments/results: File b'/Volumes/dev/code/structure-experiments/results/5thave_bvae5_var0.2_6e4_1/results.csv' does not exist
Error in parsing experiment 5thave_bvae2_var0.2_6e4_1 from basedir /Volumes/dev/code/structure-experiments/results: File b'/Volumes/dev/code/structure-experiments/results/5thave_bvae2_var0.2_6e4_1/results.csv' does not exist


# Currently running

In [74]:
networks = [       
#     "basket_fps6_z8_var0.1_6e4_1",
#     "basket_fps6_z8_var0.2_6e4_1",
#     "basket_fps15_z8_var0.1_6e4_1",
#     "basket_fps15_z8_var0.2_6e4_1",
    
#     "basket_fps6_z8_var0.01_6e4_2",
    "basket_fps15_z8_var0.05_6e4_1",
    "basket_fps15_z8_var0.01_6e4_1",
    "basket_fps6_z8_var0.05_6e4_1",
    "basket_fps6_z8_var0.01_6e4_1",
]

palette = palettes.Spectral11[:5] + palettes.Spectral11[6:]
data = make_dataframe(networks)
spaced_palette = palettes.linear_palette(palette, len(networks))
plots = []
for facet in ['loss', 'trans divergence']:
    plot = Line(data, x='step', y=facet, title="basketball" + ", " + facet,
                color=color(columns='experiment', palette=spaced_palette),
                tools='pan,wheel_zoom,box_zoom,save,reset', 
                active_scroll="wheel_zoom",
                tooltips=tooltips,
#                 plot_width=600,
#                 plot_height=600,
                legend='top_right')
#     if facet == 'loss':
#         plot.y_range = bokeh.models.Range1d(-70000, -60000)
    if facet == 'trans divergence':
        plot.y_range = bokeh.models.Range1d(0, 80)
    plots.append(plot)
show(row(children=plots, responsive=True)) #, sizing_mode="stretch_both"))

Error in parsing experiment basket_fps15_z8_var0.05_6e4_1 from basedir /Volumes/dev/code/structure-experiments/results: File b'/Volumes/dev/code/structure-experiments/results/basket_fps15_z8_var0.05_6e4_1/results.csv' does not exist
Error in parsing experiment basket_fps15_z8_var0.01_6e4_1 from basedir /Volumes/dev/code/structure-experiments/results: File b'/Volumes/dev/code/structure-experiments/results/basket_fps15_z8_var0.01_6e4_1/results.csv' does not exist
Error in parsing experiment basket_fps6_z8_var0.05_6e4_1 from basedir /Volumes/dev/code/structure-experiments/results: File b'/Volumes/dev/code/structure-experiments/results/basket_fps6_z8_var0.05_6e4_1/results.csv' does not exist
Error in parsing experiment basket_fps6_z8_var0.01_6e4_1 from basedir /Volumes/dev/code/structure-experiments/results: File b'/Volumes/dev/code/structure-experiments/results/basket_fps6_z8_var0.01_6e4_1/results.csv' does not exist


In [68]:
networks = [       
    "5thave_rbvae2_var0.2_6e4_1",
    "5thave_rbvae5_var0.2_6e4_1",
    "5thave_rbvae2_var0.05_6e4_1",
    "5thave_rbvae5_var0.05_6e4_1",
]

palette = palettes.Spectral11[:5] + palettes.Spectral11[6:]
data = make_dataframe(networks)
spaced_palette = palettes.linear_palette(palette, len(networks))
plots = []
for facet in ['loss', 'trans divergence']:
    plot = Line(data, x='step', y=facet, title="5th ave recurrent BVAE" + ", " + facet,
                color=color(columns='experiment', palette=spaced_palette),
                tools='pan,wheel_zoom,box_zoom,save,reset', 
                active_scroll="wheel_zoom",
                tooltips=tooltips,
#                 plot_width=600,
#                 plot_height=600,
                legend='top_right')
#     if facet == 'loss':
#         plot.y_range = bokeh.models.Range1d(-70000, -60000)
    if facet == 'trans divergence':
        plot.y_range = bokeh.models.Range1d(0, 80)
    plots.append(plot)
show(row(children=plots, responsive=True)) #, sizing_mode="stretch_both"))

Error in parsing experiment 5thave_rbvae2_var0.2_6e4_1 from basedir /Volumes/dev/code/structure-experiments/results: File b'/Volumes/dev/code/structure-experiments/results/5thave_rbvae2_var0.2_6e4_1/results.csv' does not exist
Error in parsing experiment 5thave_rbvae5_var0.2_6e4_1 from basedir /Volumes/dev/code/structure-experiments/results: File b'/Volumes/dev/code/structure-experiments/results/5thave_rbvae5_var0.2_6e4_1/results.csv' does not exist
Error in parsing experiment 5thave_rbvae2_var0.05_6e4_1 from basedir /Volumes/dev/code/structure-experiments/results: File b'/Volumes/dev/code/structure-experiments/results/5thave_rbvae2_var0.05_6e4_1/results.csv' does not exist
Error in parsing experiment 5thave_rbvae5_var0.05_6e4_1 from basedir /Volumes/dev/code/structure-experiments/results: File b'/Volumes/dev/code/structure-experiments/results/5thave_rbvae5_var0.05_6e4_1/results.csv' does not exist


In [69]:
networks = [       
#     "overhead_fps6_z8_var0.1_6e4_1",
#     "overhead_fps6_z8_var0.2_6e4_1",
#     "overhead_fps6_z20_var0.1_6e4_1",
#     "overhead_fps6_z20_var0.2_6e4_1",
    
    "overhead_fps15_z8_var0.05_6e4_1",
    "overhead_fps6_z8_var0.05_6e4_1",
    "overhead_fps15_z8_var0.01_6e4_1",
    "overhead_fps6_z8_var0.01_6e4_1",


]

palette = palettes.Spectral11[:5] + palettes.Spectral11[6:]
data = make_dataframe(networks)
spaced_palette = palettes.linear_palette(palette, len(networks))
plots = []
for facet in ['loss', 'trans divergence']:
    plot = Line(data, x='step', y=facet, title="overhead basketball" + ", " + facet,
                color=color(columns='experiment', palette=spaced_palette),
                tools='pan,wheel_zoom,box_zoom,save,reset', 
                active_scroll="wheel_zoom",
                tooltips=tooltips,
#                 plot_width=600,
#                 plot_height=600,
                legend='top_right')
#     if facet == 'loss':
#         plot.y_range = bokeh.models.Range1d(-70000, -60000)
    if facet == 'trans divergence':
        plot.y_range = bokeh.models.Range1d(0, 80)
    plots.append(plot)
show(row(children=plots, responsive=True)) #, sizing_mode="stretch_both"))

Error in parsing experiment overhead_fps15_z8_var0.05_6e4_1 from basedir /Volumes/dev/code/structure-experiments/results: File b'/Volumes/dev/code/structure-experiments/results/overhead_fps15_z8_var0.05_6e4_1/results.csv' does not exist
Error in parsing experiment overhead_fps6_z8_var0.05_6e4_1 from basedir /Volumes/dev/code/structure-experiments/results: File b'/Volumes/dev/code/structure-experiments/results/overhead_fps6_z8_var0.05_6e4_1/results.csv' does not exist
Error in parsing experiment overhead_fps15_z8_var0.01_6e4_1 from basedir /Volumes/dev/code/structure-experiments/results: File b'/Volumes/dev/code/structure-experiments/results/overhead_fps15_z8_var0.01_6e4_1/results.csv' does not exist
Error in parsing experiment overhead_fps6_z8_var0.01_6e4_1 from basedir /Volumes/dev/code/structure-experiments/results: File b'/Volumes/dev/code/structure-experiments/results/overhead_fps6_z8_var0.01_6e4_1/results.csv' does not exist


In [75]:
networks = [       
    "basket_fps15_z8_h50_var0.01_6e4_1",
    "basket_fps15_z8_h50_var0.05_6e4_1",
    "basket_fps15_z8_h50_var0.02_6e4_1",
    "basket_fps15_z8_h50_var0.005_3e4_1",


]

palette = palettes.Spectral11[:5] + palettes.Spectral11[6:]
data = make_dataframe(networks)
spaced_palette = palettes.linear_palette(palette, len(networks))
plots = []
for facet in ['loss', 'trans divergence']:
    plot = Line(data, x='step', y=facet, title="basketball h50 varsweep" + ", " + facet,
                color=color(columns='experiment', palette=spaced_palette),
                tools='pan,wheel_zoom,box_zoom,save,reset', 
                active_scroll="wheel_zoom",
                tooltips=tooltips,
#                 plot_width=600,
#                 plot_height=600,
                legend='top_right')
#     if facet == 'loss':
#         plot.y_range = bokeh.models.Range1d(-70000, -60000)
    if facet == 'trans divergence':
        plot.y_range = bokeh.models.Range1d(0, 80)
    plots.append(plot)
show(row(children=plots, responsive=True)) #, sizing_mode="stretch_both"))

Error in parsing experiment basket_fps15_z8_h50_var0.01_6e4_1 from basedir /Volumes/dev/code/structure-experiments/results: File b'/Volumes/dev/code/structure-experiments/results/basket_fps15_z8_h50_var0.01_6e4_1/results.csv' does not exist
Error in parsing experiment basket_fps15_z8_h50_var0.05_6e4_1 from basedir /Volumes/dev/code/structure-experiments/results: File b'/Volumes/dev/code/structure-experiments/results/basket_fps15_z8_h50_var0.05_6e4_1/results.csv' does not exist
Error in parsing experiment basket_fps15_z8_h50_var0.02_6e4_1 from basedir /Volumes/dev/code/structure-experiments/results: File b'/Volumes/dev/code/structure-experiments/results/basket_fps15_z8_h50_var0.02_6e4_1/results.csv' does not exist
Error in parsing experiment basket_fps15_z8_h50_var0.005_3e4_1 from basedir /Volumes/dev/code/structure-experiments/results: File b'/Volumes/dev/code/structure-experiments/results/basket_fps15_z8_h50_var0.005_3e4_1/results.csv' does not exist
